In [1]:
# conda install scikit-learn
# install from: http://docs.python-requests.org/en/master/
# to fix ssl installation of python packages issue
# curl https://bootstrap.pypa.io/get-pip.py | python3
# instructions to setup virtualenv
# https://www.tensorflow.org/install/install_mac
# pip3 install -r requirements.txt
# https://www.datacamp.com/community/tutorials/tensorflow-tutorial
# https://github.com/jtopor/CUNY-MSDA-661/blob/master/CIFAR-100/TF-Layers-CIFAR-100-v2.py

from __future__ import absolute_import
from __future__ import division
from __future__ import print_function

import requests
import cv2
import h5py
import scipy.misc
import numpy as np
import csv
import sklearn.model_selection as model
import pickle 
import tensorflow as tf

from csv import DictReader
from urllib.request import urlopen
from matplotlib.pyplot import imshow
from fr_utils import *
from inception_blocks_v2 import *
from skimage import transform
from tensorflow.contrib import learn
from tensorflow.contrib.learn.python.learn.estimators import model_fn as model_fn_lib

%matplotlib inline
%load_ext autoreload
%autoreload

learning_rate = 0.001
IMAGE_HEIGHT = 32
IMAGE_WIDTH = 32
IMAGE_DEPTH = 3
NUM_CLASSES = 10

np.set_printoptions(threshold=np.nan)

/Library/Frameworks/Python.framework/Versions/3.5/lib/python3.5/importlib/_bootstrap.py:222: RuntimeWarning: compiletime version 3.6 of module 'tensorflow.python.framework.fast_tensor_util' does not match runtime version 3.5
  return f(*args, **kwds)
Using TensorFlow backend.


In [5]:
def convert_input_format(data):    
    return np.transpose(
        np.reshape(data, (-1, 32, 32, 3), order="F"),
        axes=(0, 2, 1, 3)
    )

def convert_output_labels(data):
    return np.asarray(data['fine_labels'], dtype=np.int32)

def one_hot_labels(labels):
    return tf.one_hot(indices=tf.cast(labels, tf.int32), depth=100)

def unpickle(file):
    fo = open(file, "rb")
    dict = pickle.load(fo, encoding="latin1")
    fo.close()
    return dict

In [6]:
def conv_layer(input_layer, filters=32, kernel_size=[5,5]):
    # setting up the conv layer, with stride and padding
    return tf.layers.conv2d(
        inputs=input_layer,
        filters=filters,
        kernel_size=kernel_size,
        padding="same",
        activation=tf.nn.relu
    )

def maxpool_layer(conv, pool_size=[2,2], strides=2):
    return tf.layers.max_pooling2d(
        inputs=conv, pool_size=pool_size, strides=strides
    )

def dropout_layer(inputs, mode, rate=0.25):
    
    return tf.layers.dropout(
        inputs=inputs, rate=rate, training=mode == learn.ModeKeys.TRAIN
    )

def dense_layer(inputs, units, activation=tf.nn.relu):
    return tf.layers.dense(inputs=inputs, units=units, activation=activation)

def determine_loss(labels, logits, mode):
    print(mode)
#     if mode != learn.ModeKeys.INFER:
    return tf.losses.softmax_cross_entropy (
        onehot_labels=one_hot_labels(labels),
        logits=logits
    )
#     else:
#         return None
    
def determine_train_op(loss, mode):
    print(mode)
#     if mode == learn.ModeKeys.TRAIN:
    return tf.contrib.layers.optimize_loss (
        loss=loss, 
        global_step=tf.contrib.framework.get_global_step(),
        learning_rate=0.0001,
        optimizer="Adam"
    )
#     else:
#         return None
    
def generate_predictions(logits):
    return {
        "classes": tf.argmax(input=logits, axis=1),
        "probabilities": tf.nn.softmax(logits, name="softmax_tensor")
    }

def cnn_model(features, labels, mode): 
    mode = learn.ModeKeys.TRAIN if mode == "train" else learn.ModeKeys.INFER
    input_layer = tf.convert_to_tensor(features)
    
    # cnn layer 1
    conv1 = conv_layer(input_layer)
    conv2 = conv_layer(conv1)
    
    # pooling layer 1 
    pool1 = maxpool_layer(conv2)
    
    # dropout operation
    dropout1 = dropout_layer(pool1, mode)
    
    # cnn layer 2 
    conv3 = conv_layer(dropout1, 64, [3, 3])
    conv4 = conv_layer(conv3, 64, [3, 3])
    
    # pooling layer 2
    pool2 = maxpool_layer(conv4)
    
    # dropout operation
    dropout2 = dropout_layer(pool2, mode)
    
    # flatten tensor into a batch of vectors
    pool2_flat = tf.reshape(dropout2, [-1, 8 * 8 * 64])
    
    # dense layer 
    dense1 = dense_layer(pool2_flat, 1024)
    
    # flatten tensor again
    dropout3 = dropout_layer(dense1, mode, 0.4)
    
    # second fully connected layer 
    dense2 = tf.layers.dense(inputs=dropout3, units=512)
    
    # dropout operation
    dropout4 = dropout_layer(dense2, mode, 0.4)
    
    # logits layer
    logits = tf.layers.dense(inputs=dropout4, units=100)
    
    loss = determine_loss(labels, logits, mode)
    train_op = determine_train_op(loss, mode)
    predictions = generate_predictions(logits)
    
    return model_fn_lib.ModelFnOps(
        mode=mode, predictions=predictions, loss=loss, train_op=train_op
    )
    

In [7]:
def generate_accuracy_metric():
    # configure the accuracy metric
    return {
        "accuracy": learn.MetricSpec (
            metric_fn=tf.metrics.accuracy, prediction_key="classes"
        )
    }

def serving_input_fn():
    receiver_tensor = {"images": tf.placeholder(
        shape=[None, IMAGE_HEIGHT, IMAGE_WIDTH, IMAGE_DEPTH], dtype=tf.float32)}
    features = receiver_tensor
    return tf.estimator.export.ServingInputReceiver(features, receiver_tensor)

def print_evaluate_model(cifar_classifier, data, labels, epoches, subset):
    small_train = np.array_split(data, epoches)[subset]
    small_labels = np.array_split(labels, epoches)[subset]
    evaluate_results = cifar_classifier.evaluate(
        x=small_train, y=small_labels, metrics=generate_accuracy_metric()
    )
    print(evaluate_results)
    return evaluate_results

def setup_and_train_model():
    dataset = unpickle("./datasets/cifar-100-parsed/cifar-100-python/train")
    data = dataset["data"]
    data = data.astype("float32")
    train_data = convert_input_format(data)
    train_labels = convert_output_labels(dataset)
    model_ckpt = "/tmp/cifar100"
    
    exporter = tf.estimator.LatestExporter (
        name="Servo",
        serving_input_receiver_fn=serving_input_fn,
        assets_extra=None,
        as_text=False,
        exports_to_keep=5
    )
    
    # create custom estimator
    cifar_classifier = learn.Estimator (
        model_fn=cnn_model, model_dir="/tmp/cifar100" 
    )
    
    # log predictions
    tensors_to_log = {"probabilities": "softmax_tensor"}
    logging_hook = tf.train.LoggingTensorHook (
        tensors=tensors_to_log, every_n_iter=100
    )
    
    # train the model
    with tf.device("/cpu:0"):
        cifar_classifier.fit (
            x=train_data,
            y=train_labels,
            batch_size=64, 
            steps=5240,
            monitors=[logging_hook]
        )
    
    full_model_dir = cifar_classifier.export_savedmodel(
        "./models/cifar-100", serving_input_fn()
    )
    return cifar_classifier


def test_model(cifar_classifier):
    dataset = unpickle("./datasets/cifar-100-parsed/cifar-100-python/test")
    data = dataset["data"]
    data = data.astype("float32")
    test_data = convert_input_format(data)
    test_labels = convert_output_labels(dataset)
    
    # evaluate all test data and print results
    acc = 0
    e_loss = 0
    n_batches = 20
    for i in range (0, n_batches - 1):
        small_eval =  np.array_split(test_data, n_batches)[i]
        small_labs =  np.array_split(test_labels, n_batches)[i]
        eval_results = cifar_classifier.evaluate(
          x=small_eval, y=small_labs, metrics=generate_accuracy_metric())
        print(eval_results)
        acc += eval_results["accuracy"]
        e_loss += eval_results["loss"]

    overall_acc = acc / n_batches
    overall_loss = e_loss/ n_batches
    print("Eval Accuracy = ", overall_acc)
    print("Eval Loss = ", overall_loss) 

In [8]:
classifier = setup_and_train_model()

Instructions for updating:
Please replace uses of any Estimator from tf.contrib.learn with an Estimator from tf.estimator.*
Instructions for updating:
When switching to tf.estimator.Estimator, use tf.estimator.RunConfig instead.
INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_model_dir': '/tmp/cifar100', '_save_checkpoints_steps': None, '_save_summary_steps': 100, '_log_step_count_steps': 100, '_session_config': None, '_num_ps_replicas': 0, '_keep_checkpoint_max': 5, '_save_checkpoints_secs': 600, '_environment': 'local', '_tf_config': gpu_options {
  per_process_gpu_memory_fraction: 1.0
}
, '_train_distribute': None, '_task_id': 0, '_evaluation_master': '', '_tf_random_seed': None, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x13b4992b0>, '_device_fn': None, '_num_worker_replicas': 0, '_keep_checkpoint_every_n_hours': 10000, '_master': '', '_task_type': None, '_is_chief': True}
Instructions for updating:
Estimator is decoupled f

INFO:tensorflow:loss = 1.199364, step = 33529
INFO:tensorflow:global_step/sec: 2.17808
INFO:tensorflow:probabilities = [[0.0011346  0.00009847 0.22312145 0.00010139 0.00028733 0.04606781
  0.00039127 0.00186803 0.00019628 0.0025518  0.00019911 0.00888768
  0.00008568 0.00018457 0.00000569 0.00015623 0.00193858 0.0000638
  0.00009113 0.00000346 0.00193187 0.00017406 0.00019212 0.00159514
  0.00231168 0.00048228 0.00007278 0.00009415 0.00001358 0.00021372
  0.00037552 0.00047428 0.0003212  0.00317269 0.00129787 0.30350566
  0.0001847  0.00067445 0.00001549 0.00279241 0.09916996 0.00001007
  0.00003806 0.00017457 0.00098372 0.02413557 0.00594187 0.00001047
  0.00002227 0.00008343 0.00177385 0.0010712  0.00000235 0.00037116
  0.07848122 0.00149343 0.00003143 0.00160728 0.00028965 0.00011217
  0.00002917 0.00279446 0.00021722 0.00000283 0.00011589 0.0001381
  0.00004306 0.00002252 0.00001753 0.00004878 0.00132457 0.00783342
  0.00006463 0.00100667 0.00014997 0.00009272 0.00036529 0.00019073

INFO:tensorflow:loss = 0.8451397, step = 33629 (45.915 sec)
INFO:tensorflow:global_step/sec: 2.60317
INFO:tensorflow:probabilities = [[0.00000046 0.00000089 0.00002053 0.00001749 0.0000815  0.0000009
  0.00003685 0.0000103  0.00023743 0.00000007 0.00000002 0.00001684
  0.00002601 0.0001467  0.00018598 0.003467   0.00000008 0.00001584
  0.00000657 0.00041006 0.00000115 0.00004895 0.00000065 0.00000003
  0.0000018  0.00000027 0.00059933 0.00150218 0.00000004 0.00224332
  0.00000084 0.00003531 0.00002274 0.00018957 0.00044638 0.00000714
  0.00000048 0.00018229 0.00165332 0.00000001 0.00000632 0.00002829
  0.00024618 0.00054935 0.00011752 0.00115154 0.00007203 0.00000485
  0.00006952 0.00000184 0.00000146 0.00016518 0.00001155 0.00000029
  0.00000255 0.00002658 0.00075035 0.00000135 0.00000998 0.00006622
  0.00000012 0.00000004 0.00000236 0.00000008 0.00001875 0.00000425
  0.00001995 0.00001562 0.0000052  0.00000119 0.00000144 0.00000118
  0.00006982 0.00000006 0.00005052 0.00000559 0.0000

INFO:tensorflow:loss = 0.9091654, step = 33729 (38.417 sec)
INFO:tensorflow:global_step/sec: 2.29601
INFO:tensorflow:probabilities = [[0.00000004 0.00002271 0.00027161 0.         0.         0.93488896
  0.00000007 0.00000001 0.0000035  0.00153873 0.00025882 0.00029458
  0.00000365 0.03440122 0.00000003 0.00000002 0.00479395 0.00000127
  0.00000008 0.         0.00568248 0.00000001 0.00048271 0.00000009
  0.00000001 0.00000049 0.00000061 0.00000011 0.         0.00000001
  0.         0.         0.0000455  0.         0.00000002 0.00005535
  0.00000225 0.00001185 0.00000001 0.         0.0008543  0.00000088
  0.0000007  0.00000005 0.00000034 0.00000471 0.00006177 0.
  0.00010505 0.00000001 0.         0.00000093 0.         0.00009827
  0.00000078 0.         0.00000007 0.00000024 0.000605   0.00000002
  0.         0.00142009 0.00000009 0.         0.00000001 0.00000006
  0.00000001 0.         0.         0.00000013 0.         0.00000002
  0.         0.00000001 0.         0.         0.00000002 0.

INFO:tensorflow:loss = 1.3798509, step = 33829 (43.551 sec)
INFO:tensorflow:global_step/sec: 2.29762
INFO:tensorflow:probabilities = [[0.         0.         0.         0.         0.         0.
  0.         0.         0.         0.9999989  0.         0.
  0.         0.         0.         0.         0.         0.
  0.         0.         0.         0.         0.         0.
  0.         0.         0.         0.         0.         0.
  0.         0.         0.         0.         0.         0.
  0.         0.         0.         0.         0.         0.
  0.         0.         0.         0.         0.         0.
  0.         0.         0.         0.         0.         0.
  0.         0.         0.         0.         0.         0.
  0.         0.         0.         0.         0.         0.
  0.         0.         0.         0.0000011  0.         0.
  0.         0.         0.         0.         0.         0.
  0.         0.         0.         0.         0.         0.
  0.         0.         0. 

...

INFO:tensorflow:loss = 0.9482347, step = 38429 (47.594 sec)
INFO:tensorflow:global_step/sec: 2.29379
INFO:tensorflow:probabilities = [[0.00000002 0.00000008 0.00000002 0.00000115 0.00001203 0.00000032
  0.00000001 0.00000004 0.00000005 0.00000003 0.00000001 0.00000012
  0.00036882 0.00000018 0.00000001 0.00000007 0.00000001 0.00000056
  0.00000051 0.         0.         0.00000002 0.00000025 0.00002133
  0.00000007 0.00000006 0.00000084 0.00006095 0.00000001 0.00000178
  0.988241   0.00000001 0.00007148 0.00000006 0.00000006 0.00000054
  0.00000001 0.00000198 0.00000102 0.00000695 0.00000009 0.
  0.00000009 0.         0.00000003 0.00000017 0.00000003 0.00000001
  0.00000022 0.000103   0.0000048  0.00000002 0.00000007 0.00000001
  0.00000001 0.00003277 0.00006997 0.00000001 0.00000377 0.00000294
  0.00000005 0.00000002 0.00000002 0.00000047 0.00000023 0.00000078
  0.00000296 0.00002605 0.00000014 0.00000172 0.         0.00006018
  0.00018603 0.00121349 0.00000053 0.00000004 0.0000006  0.

INFO:tensorflow:loss = 0.95798874, step = 38529 (43.609 sec)
INFO:tensorflow:global_step/sec: 2.25474
INFO:tensorflow:probabilities = [[0.00006297 0.00062122 0.00000076 0.00000002 0.0000049  0.00129077
  0.00000058 0.00000068 0.         0.0000003  0.9468903  0.00000026
  0.         0.00000037 0.0000017  0.00000004 0.00052271 0.00000007
  0.00145501 0.00000001 0.00789915 0.00000001 0.00002682 0.00000089
  0.00009396 0.00850259 0.00082309 0.00000023 0.00053888 0.00000004
  0.00000064 0.         0.0002553  0.00000003 0.00000047 0.00000002
  0.00140237 0.00000002 0.         0.00696941 0.00000137 0.00000032
  0.00000007 0.00000148 0.00004808 0.0000018  0.00000003 0.00002512
  0.00000005 0.00000605 0.00017955 0.0000034  0.00000026 0.00049333
  0.00000112 0.000002   0.00000002 0.00002179 0.00000084 0.00000068
  0.00000444 0.00089418 0.00003152 0.00000735 0.00000043 0.00000066
  0.00000004 0.00001177 0.00000017 0.00000029 0.00000687 0.00000122
  0.00000036 0.00000139 0.00089748 0.00000059 0.00

INFO:tensorflow:loss = 1.2957854, step = 38629 (44.335 sec)
INFO:tensorflow:Saving checkpoints for 38677 into /tmp/cifar100/model.ckpt.
INFO:tensorflow:global_step/sec: 2.28603
INFO:tensorflow:probabilities = [[0.00003299 0.00003682 0.00040045 0.00003486 0.00497355 0.00009355
  0.00067166 0.02496116 0.00002541 0.00002456 0.00090942 0.00026132
  0.00005757 0.00055019 0.00343096 0.00004283 0.00007796 0.00000593
  0.00026902 0.00128631 0.00001224 0.00021695 0.01741178 0.00002222
  0.00143771 0.00008384 0.00423114 0.00440847 0.00001678 0.00006966
  0.00001283 0.00020807 0.00870711 0.00003902 0.00052299 0.00060036
  0.00062336 0.00019038 0.001827   0.00024882 0.00000409 0.00002612
  0.00077842 0.00018402 0.00169936 0.00097951 0.0000238  0.00000109
  0.0000269  0.00000038 0.1913798  0.03008641 0.00000531 0.00001391
  0.00001135 0.12056333 0.00006778 0.00004611 0.00000927 0.00002557
  0.0000011  0.00670674 0.00005347 0.00541068 0.02451676 0.07303657
  0.01751944 0.00125044 0.00000283 0.000004

INFO:tensorflow:loss = 0.7945504, step = 38729 (43.740 sec)
INFO:tensorflow:Saving checkpoints for 38768 into /tmp/cifar100/model.ckpt.
INFO:tensorflow:Loss for final step: 0.85991883.


NameError: name 'IMAGE_HEIGHT' is not defined

In [35]:
test_model(classifier)

infer
infer
INFO:tensorflow:Starting evaluation at 2018-08-03-06:27:22
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/cifar100/model.ckpt-33528
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Finished evaluation at 2018-08-03-06:27:27
INFO:tensorflow:Saving dict for global step 33528: accuracy = 0.424, global_step = 33528, loss = 2.4908679
{'global_step': 33528, 'loss': 2.4908679, 'accuracy': 0.424}
infer
infer
INFO:tensorflow:Starting evaluation at 2018-08-03-06:27:31
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/cifar100/model.ckpt-33528
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Finished evaluation at 2018-08-03-06:27:36
INFO:tensorflow:Saving dict for global step 33528: accuracy = 0.442, global_step = 33528, loss = 2.2866387
{'global_step': 33528, 'loss': 2.2866387, 'accuracy': 0.442}
infer
infer
INFO:t

{'global_step': 33528, 'loss': 2.2949243, 'accuracy': 0.448}
infer
infer
INFO:tensorflow:Starting evaluation at 2018-08-03-06:28:53
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/cifar100/model.ckpt-33528
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Finished evaluation at 2018-08-03-06:28:56
INFO:tensorflow:Saving dict for global step 33528: accuracy = 0.448, global_step = 33528, loss = 2.304841
{'global_step': 33528, 'loss': 2.304841, 'accuracy': 0.448}
infer
infer
INFO:tensorflow:Starting evaluation at 2018-08-03-06:28:58
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from /tmp/cifar100/model.ckpt-33528
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Finished evaluation at 2018-08-03-06:29:01
INFO:tensorflow:Saving dict for global step 33528: accuracy = 0.42, global_step = 33528, loss = 2.4275591
{'global_step': 33528